In [ ]:
pip install category_encoders

     |████████████████████████████████| 81kB 5.1MB/s 


In [ ]:
import pandas as pd
import numpy as np
import datetime as datetime
import calendar

In [ ]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
%matplotlib inline
import matplotlib.pyplot as plt
from sklearn import tree
from sklearn.model_selection import train_test_split 

In [ ]:
from sklearn.metrics import log_loss 
from category_encoders.target_encoder import TargetEncoder 

/usr/local/lib/python3.7/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [ ]:
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split, KFold, cross_validate
from sklearn.linear_model import RidgeClassifier, SGDClassifier, LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, ExtraTreesClassifier, BaggingClassifier, VotingClassifier, RandomTreesEmbedding
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import GridSearchCV

In [ ]:
from google.colab import files
 
files.upload()  

Saving Test_TP2_Datos_2020-2C.csv to Test_TP2_Datos_2020-2C.csv
Saving Train_TP2_Datos_2020-2C.csv to Train_TP2_Datos_2020-2C.csv


{'Test_TP2_Datos_2020-2C.csv': b'\xef\xbb\xbfID,Region,Territory,"Pricing, Delivery_Terms_Quote_Appr","Pricing, Delivery_Terms_Approved",Bureaucratic_Code_0_Approval,Bureaucratic_Code_0_Approved,Submitted_for_Approval,Bureaucratic_Code,Account_Created_Date,Source ,Billing_Country,Account_Name,Opportunity_Name,Opportunity_ID,Sales_Contract_No,Account_Owner,Opportunity_Owner,Account_Type,Opportunity_Type,Quote_Type,Delivery_Terms,Opportunity_Created_Date,Brand,Product_Type,Size,Product_Category_B,Price,Currency,Last_Activity,Quote_Expiry_Date,Last_Modified_Date,Last_Modified_By,Product_Family,Product_Name,ASP_Currency,ASP,ASP_(converted)_Currency,ASP_(converted),Planned_Delivery_Start_Date,Planned_Delivery_End_Date,Month,Delivery_Quarter,Delivery_Year,Actual_Delivery_Date,TRF,Total_Amount_Currency,Total_Amount,Total_Taxable_Amount_Currency,Total_Taxable_Amount,Prod_Category_A\r\n6140,EMEA,Germany,1,1,1,1,0,Bureaucratic_Code_4,7/5/2017,Source_7,Germany,Account_Name_978,Opportunity_Name_61

In [ ]:
df_train = pd.read_csv('Train_TP2_Datos_2020-2C.csv')
df_test = pd.read_csv('Test_TP2_Datos_2020-2C.csv')

In [ ]:
df_train

ID    Region  ...        Stage       Prod_Category_A
0      27761      EMEA  ...  Closed Lost  Prod_Category_A_None
1      27760      EMEA  ...   Closed Won  Prod_Category_A_None
2      27446  Americas  ...   Closed Won  Prod_Category_A_None
3      16808  Americas  ...  Closed Lost  Prod_Category_A_None
4      16805  Americas  ...  Closed Lost  Prod_Category_A_None
...      ...       ...  ...          ...                   ...
16942   8781      EMEA  ...   Closed Won  Prod_Category_A_None
16943   8786      EMEA  ...   Closed Won  Prod_Category_A_None
16944   8792      EMEA  ...   Closed Won  Prod_Category_A_None
16945  28561  Americas  ...  Closed Lost  Prod_Category_A_None
16946  28318  Americas  ...  Closed Lost  Prod_Category_A_None

[16947 rows x 52 columns]

In [ ]:
df_test

ID    Region  ... Total_Taxable_Amount       Prod_Category_A
0      6140      EMEA  ...             367419.0  Prod_Category_A_None
1      6146      EMEA  ...             367419.0  Prod_Category_A_None
2      6151      EMEA  ...             367419.0  Prod_Category_A_None
3      6118      EMEA  ...             757783.5  Prod_Category_A_None
4      6124      EMEA  ...             757783.5  Prod_Category_A_None
...     ...       ...  ...                  ...                   ...
2546  16345      EMEA  ...             147750.0  Prod_Category_A_None
2547  15218  Americas  ...              45054.9  Prod_Category_A_None
2548  15224  Americas  ...             100122.0  Prod_Category_A_None
2549   7286  Americas  ...             143220.0  Prod_Category_A_None
2550  11263      EMEA  ...             871020.8  Prod_Category_A_None

[2551 rows x 51 columns]

In [ ]:
df_test.info()

In [ ]:
df_train['Opportunity_Created_Date'] = pd.to_datetime(df_train['Opportunity_Created_Date'])
df_train['años'] = df_train['Opportunity_Created_Date'].dt.year
df_train['meses'] = df_train['Opportunity_Created_Date'].dt.month

In [ ]:
df_ML_train = df_train[['años', 'meses', 'TRF', 'Region', 'Territory', 'Opportunity_Owner', 'Opportunity_Type', 'Stage']]
df_ML_train = df_ML_train.loc[df_ML_train['Stage'].isin (['Closed Won', 'Closed Lost'])]

In [ ]:
df_ML_train

años  meses  TRF  ... Opportunity_Owner     Opportunity_Type        Stage
0      2015     12   10  ...    Person_Name_18   Opportunity_Type_1  Closed Lost
1      2015     12    0  ...    Person_Name_20   Opportunity_Type_1   Closed Won
2      2015     12    0  ...     Person_Name_8   Opportunity_Type_1   Closed Won
3      2015     12   14  ...     Person_Name_8  Opportunity_Type_19  Closed Lost
4      2015     12   25  ...     Person_Name_8  Opportunity_Type_19  Closed Lost
...     ...    ...  ...  ...               ...                  ...          ...
16942  2015     12    0  ...    Person_Name_13   Opportunity_Type_1   Closed Won
16943  2015     12    0  ...    Person_Name_13   Opportunity_Type_1   Closed Won
16944  2015     12    0  ...    Person_Name_13   Opportunity_Type_1   Closed Won
16945  2015     12    4  ...     Person_Name_3   Opportunity_Type_1  Closed Lost
16946  2015     12   40  ...     Person_Name_3  Opportunity_Type_19  Closed Lost

[16883 rows x 8 columns]

In [ ]:
cambio_binario = {'Closed Lost' : 0, 'Closed Won' : 1}
df_ML_train['Stage'] = df_ML_train['Stage'].map(cambio_binario)
df_ML_train.sort_values(['años', 'meses'], ascending=True, inplace=True)
df_ML_train

años  meses  TRF  ... Opportunity_Owner     Opportunity_Type Stage
16104  2013     11    2  ...    Person_Name_16   Opportunity_Type_1     0
16105  2014      3   20  ...     Person_Name_4  Opportunity_Type_19     0
16106  2014      3    0  ...     Person_Name_8   Opportunity_Type_1     0
16107  2014      3    0  ...     Person_Name_8   Opportunity_Type_1     0
16108  2014      5    6  ...    Person_Name_12  Opportunity_Type_19     1
...     ...    ...  ...  ...               ...                  ...   ...
16099  2018     12    0  ...    Person_Name_32   Opportunity_Type_1     1
16100  2018     12    1  ...     Person_Name_8   Opportunity_Type_7     1
16101  2018     12    0  ...    Person_Name_38   Opportunity_Type_7     1
16102  2018     12    0  ...    Person_Name_38   Opportunity_Type_7     1
16103  2018     12    0  ...    Person_Name_38   Opportunity_Type_7     1

[16883 rows x 8 columns]

VAMOS A ENCODEAR TODOS LOS FEATURES CATEGORICOS PARA PODER USARLOS EN EL MODELO

In [ ]:
cat_cols = df_ML_train.select_dtypes(include='object').columns
cat_cols

Index(['Region', 'Territory', 'Opportunity_Owner', 'Opportunity_Type'], dtype='object')

In [ ]:
df_ML_cat = df_ML_train[cat_cols]
df_ML_cat

Region    Territory Opportunity_Owner     Opportunity_Type
16104      EMEA       France    Person_Name_16   Opportunity_Type_1
16105      APAC  Philippines     Person_Name_4  Opportunity_Type_19
16106  Americas   NW America     Person_Name_8   Opportunity_Type_1
16107  Americas   NW America     Person_Name_8   Opportunity_Type_1
16108  Americas         None    Person_Name_12  Opportunity_Type_19
...         ...          ...               ...                  ...
16099     Japan        Japan    Person_Name_32   Opportunity_Type_1
16100  Americas   NW America     Person_Name_8   Opportunity_Type_7
16101  Americas   SE America    Person_Name_38   Opportunity_Type_7
16102  Americas   SE America    Person_Name_38   Opportunity_Type_7
16103  Americas   SE America    Person_Name_38   Opportunity_Type_7

[16883 rows x 4 columns]

In [ ]:
enc = TargetEncoder(cols=df_ML_cat, handle_unknown='value', return_df=False)
enc.fit(df_ML_cat,df_ML_train['Stage'])
df_mean_encoding = pd.DataFrame(enc.transform(df_ML_cat))

/usr/local/lib/python3.7/dist-packages/category_encoders/utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):


In [ ]:
df_mean_encoding.rename(columns={0:'Region', 1:'Territory', 2:'Opportunity_Owner', 3:'Opportunity_Type'}, inplace=True)
df_mean_encoding

Region  Territory  Opportunity_Owner  Opportunity_Type
0      0.530258   0.318486           0.286996          0.533953
1      0.583205   0.385321           0.471533          0.211223
2      0.455886   0.623718           0.587201          0.533953
3      0.455886   0.623718           0.587201          0.533953
4      0.455886   0.609115           0.304348          0.211223
...         ...        ...                ...               ...
16878  0.682481   0.807692           0.783942          0.533953
16879  0.455886   0.623718           0.587201          0.684201
16880  0.455886   0.382413           0.348000          0.684201
16881  0.455886   0.382413           0.348000          0.684201
16882  0.455886   0.382413           0.348000          0.684201

[16883 rows x 4 columns]

In [ ]:
df_ML_train = pd.concat([df_ML_train.drop(columns=cat_cols), df_mean_encoding], axis=1)
df_ML_train

años  meses   TRF  ...  Territory  Opportunity_Owner  Opportunity_Type
0      2015.0   12.0  10.0  ...   0.318486           0.286996          0.533953
1      2015.0   12.0   0.0  ...   0.385321           0.471533          0.211223
2      2015.0   12.0   0.0  ...   0.623718           0.587201          0.533953
3      2015.0   12.0  14.0  ...   0.623718           0.587201          0.533953
4      2015.0   12.0  25.0  ...   0.609115           0.304348          0.211223
...       ...    ...   ...  ...        ...                ...               ...
16942  2015.0   12.0   0.0  ...        NaN                NaN               NaN
16943  2015.0   12.0   0.0  ...        NaN                NaN               NaN
16944  2015.0   12.0   0.0  ...        NaN                NaN               NaN
16945  2015.0   12.0   4.0  ...        NaN                NaN               NaN
16946  2015.0   12.0  40.0  ...        NaN                NaN               NaN

[16947 rows x 8 columns]

In [ ]:
df_ML_train = df_ML_train.dropna()
df_ML_train

años  meses   TRF  ...  Territory  Opportunity_Owner  Opportunity_Type
0      2015.0   12.0  10.0  ...   0.318486           0.286996          0.533953
1      2015.0   12.0   0.0  ...   0.385321           0.471533          0.211223
2      2015.0   12.0   0.0  ...   0.623718           0.587201          0.533953
3      2015.0   12.0  14.0  ...   0.623718           0.587201          0.533953
4      2015.0   12.0  25.0  ...   0.609115           0.304348          0.211223
...       ...    ...   ...  ...        ...                ...               ...
16878  2015.0   12.0   0.0  ...   0.807692           0.783942          0.533953
16879  2015.0   12.0   0.0  ...   0.623718           0.587201          0.684201
16880  2015.0   12.0   0.0  ...   0.382413           0.348000          0.684201
16881  2015.0   12.0   0.0  ...   0.382413           0.348000          0.684201
16882  2015.0   12.0   0.0  ...   0.382413           0.348000          0.684201

[16819 rows x 8 columns]

PREPARAMOS PARA ENSEÑAR AL SET DE ENTRENAMIENTO

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(df_ML_train.drop('Stage', axis=1), df_ML_train['Stage'], test_size=.20, random_state=42)

In [ ]:
clfs = []
seed = 3

clfs.append(("LogReg", 
             Pipeline([("Scaler", StandardScaler()),
                       ("LogReg", LogisticRegression(n_jobs=-1, random_state=42))])))



clfs.append(("RandomForestClassifier", 
             Pipeline([("Scaler", StandardScaler()),
                       ("RandomForest", RandomForestClassifier(n_estimators=200, n_jobs=-1, 
                                                               random_state=42))]))) 

clfs.append(("GradientBoostingClassifier", 
             Pipeline([("Scaler", StandardScaler()),
                       ("GradientBoosting", GradientBoostingClassifier(n_estimators=200,
                                                                       random_state=42))]))) 

#clfs.append(("RidgeClassifier", 
#            Pipeline([("Scaler", StandardScaler()),
#                       ("RidgeClassifier", RidgeClassifier(random_state=42))])))

clfs.append(("BaggingRidgeClassifier",
             Pipeline([("Scaler", StandardScaler()),
                       ("BaggingClassifier", BaggingClassifier(n_jobs=-1, random_state=42))])))

clfs.append(("ExtraTreesClassifier",
             Pipeline([("Scaler", StandardScaler()),
                       ("ExtraTrees", ExtraTreesClassifier(n_jobs=-1, random_state=42))])))


scoring = 'neg_log_loss'
n_folds = 5

results, names  = [], [] 

for name, model  in clfs:
    kfold = KFold(n_splits=n_folds, random_state=seed)
    cv_results = cross_val_score(model, X_train, y_train, 
                                 cv= n_folds, scoring=scoring,
                                 n_jobs=-1)    
    names.append(name)
    results.append(cv_results)    
    msg = "%s: %f (+/- %f)" % (name, -cv_results.mean(),  cv_results.std())
    print(msg)

/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:296: FutureWarning: Setting a random_state has no effect since shuffle is False. This will raise an error in 0.24. You should leave random_state to its default (None), or set shuffle=True.
  FutureWarning


KeyboardInterrupt: ignored

BUSCAMOS LOS HIPER PARAMETROS PARA RANDOMFOREST

In [ ]:
parametros = {'n_estimators' : [100, 150, 200, 300, 400], 'min_samples_split' : [2,3,4]}
#RandomForestClassifier(n_estimators=, max_depth=, min_samples_split=,)

rdmforest = RandomForestClassifier()
clf = GridSearchCV(rdmforest, parametros)

In [ ]:
clf.fit(X = X_train, y = y_train)

GridSearchCV(cv=None, error_score=nan,
             estimator=RandomForestClassifier(bootstrap=True, ccp_alpha=0.0,
                                              class_weight=None,
                                              criterion='gini', max_depth=None,
                                              max_features='auto',
                                              max_leaf_nodes=None,
                                              max_samples=None,
                                              min_impurity_decrease=0.0,
                                              min_impurity_split=None,
                                              min_samples_leaf=1,
                                              min_samples_split=2,
                                              min_weight_fraction_leaf=0.0,
                                              n_estimators=100, n_jobs=None,
                                              oob_score=False,
                                              ra

In [ ]:
clf.cv_results_

{'mean_fit_time': array([0.84969811, 1.26180983, 1.6798234 , 2.52029443, 3.39167295,
        0.83132076, 1.22730799, 1.64693661, 2.47913623, 3.29364305,
        0.81813993, 1.2196125 , 1.62056212, 2.44299188, 3.24629688]),
 'mean_score_time': array([0.07042232, 0.10582185, 0.13890762, 0.20930605, 0.28005929,
        0.07022996, 0.10413685, 0.1371665 , 0.20895147, 0.2747746 ,
        0.0687089 , 0.10118613, 0.13878446, 0.20188022, 0.2718019 ]),
 'mean_test_score': array([0.73206986, 0.73325901, 0.73206986, 0.73392791, 0.73467113,
        0.73363062, 0.73548867, 0.73392791, 0.73474545, 0.73556299,
        0.73742103, 0.73586027, 0.73719807, 0.73675214, 0.73690078]),
 'param_min_samples_split': masked_array(data=[2, 2, 2, 2, 2, 3, 3, 3, 3, 3, 4, 4, 4, 4, 4],
              mask=[False, False, False, False, False, False, False, False,
                    False, False, False, False, False, False, False],
        fill_value='?',
             dtype=object),
 'param_n_estimators': masked_array(

In [ ]:
preds = clf.predict_proba(X_test)
error = log_loss(y_test, preds)
print('error: %f' %(error))

error: 0.596290


**PRUEBA DE SET TEST**

In [ ]:
df_test['Opportunity_Created_Date'] = pd.to_datetime(df_test['Opportunity_Created_Date'])
df_test['años'] = df_test['Opportunity_Created_Date'].dt.year
df_test['meses'] = df_test['Opportunity_Created_Date'].dt.month
df_ML_test = df_test[['años', 'meses', 'TRF', 'Region', 'Territory', 'Opportunity_Owner', 'Opportunity_Type', 'Opportunity_ID']]
df_ML_test


años  meses  TRF  ... Opportunity_Owner    Opportunity_Type Opportunity_ID
0     2019      4    0  ...    Person_Name_13  Opportunity_Type_8          10689
1     2019      4    0  ...    Person_Name_13  Opportunity_Type_8          10689
2     2019      4    0  ...    Person_Name_13  Opportunity_Type_8          10689
3     2019      4    1  ...    Person_Name_13  Opportunity_Type_8          10690
4     2019      4    0  ...    Person_Name_13  Opportunity_Type_8          10690
...    ...    ...  ...  ...               ...                 ...            ...
2546  2019      4    0  ...    Person_Name_13  Opportunity_Type_1          12364
2547  2019      4    0  ...    Person_Name_38  Opportunity_Type_1          12365
2548  2019      4    0  ...    Person_Name_38  Opportunity_Type_1          12366
2549  2019      4    0  ...     Person_Name_9  Opportunity_Type_7          12367
2550  2019      4    3  ...    Person_Name_16  Opportunity_Type_1          12368

[2551 rows x 8 columns]

In [ ]:
df_ML_test_cat = df_ML_test[cat_cols]
df_ML_test_cat

Region   Territory Opportunity_Owner    Opportunity_Type
0         EMEA     Germany    Person_Name_13  Opportunity_Type_8
1         EMEA     Germany    Person_Name_13  Opportunity_Type_8
2         EMEA     Germany    Person_Name_13  Opportunity_Type_8
3         EMEA     Germany    Person_Name_13  Opportunity_Type_8
4         EMEA     Germany    Person_Name_13  Opportunity_Type_8
...        ...         ...               ...                 ...
2546      EMEA         KSA    Person_Name_13  Opportunity_Type_1
2547  Americas  SE America    Person_Name_38  Opportunity_Type_1
2548  Americas  SE America    Person_Name_38  Opportunity_Type_1
2549  Americas  NE America     Person_Name_9  Opportunity_Type_7
2550      EMEA     Belgium    Person_Name_16  Opportunity_Type_1

[2551 rows x 4 columns]

In [ ]:
enc = TargetEncoder(cols=df_ML_test_cat, handle_unknown='value', return_df=False)
enc.fit(df_ML_test_cat,df_ML_test['Opportunity_ID'])
df_mean_encoding_test = pd.DataFrame(enc.transform(df_ML_test_cat))
df_mean_encoding_test

/usr/local/lib/python3.7/dist-packages/category_encoders/utils.py:21: FutureWarning: is_categorical is deprecated and will be removed in a future version.  Use is_categorical_dtype instead
  elif pd.api.types.is_categorical(cols):


0             1             2             3
0     11503.219570  11503.439560  11531.962733  11593.290076
1     11503.219570  11503.439560  11531.962733  11593.290076
2     11503.219570  11503.439560  11531.962733  11593.290076
3     11503.219570  11503.439560  11531.962733  11593.290076
4     11503.219570  11503.439560  11531.962733  11593.290076
...            ...           ...           ...           ...
2546  11503.219570  11789.571092  11531.962733  11504.536007
2547  11583.837598  11621.935185  11552.820513  11504.536007
2548  11583.837598  11621.935185  11552.820513  11504.536007
2549  11583.837598  11689.899441  11707.037037  11647.177469
2550  11503.219570  11689.525424  11625.743119  11504.536007

[2551 rows x 4 columns]

In [ ]:
df_mean_encoding_test.rename(columns={0:'Region', 1:'Territory', 2:'Opportunity_Owner', 3:'Opportunity_Type'}, inplace=True)
df_mean_encoding_test

Region     Territory  Opportunity_Owner  Opportunity_Type
0     11503.219570  11503.439560       11531.962733      11593.290076
1     11503.219570  11503.439560       11531.962733      11593.290076
2     11503.219570  11503.439560       11531.962733      11593.290076
3     11503.219570  11503.439560       11531.962733      11593.290076
4     11503.219570  11503.439560       11531.962733      11593.290076
...            ...           ...                ...               ...
2546  11503.219570  11789.571092       11531.962733      11504.536007
2547  11583.837598  11621.935185       11552.820513      11504.536007
2548  11583.837598  11621.935185       11552.820513      11504.536007
2549  11583.837598  11689.899441       11707.037037      11647.177469
2550  11503.219570  11689.525424       11625.743119      11504.536007

[2551 rows x 4 columns]

In [ ]:
df_ML_test = pd.concat([df_ML_test.drop(columns=cat_cols), df_mean_encoding_test], axis=1)
df_ML_test

años  meses  TRF  ...     Territory  Opportunity_Owner  Opportunity_Type
0     2019      4    0  ...  11503.439560       11531.962733      11593.290076
1     2019      4    0  ...  11503.439560       11531.962733      11593.290076
2     2019      4    0  ...  11503.439560       11531.962733      11593.290076
3     2019      4    1  ...  11503.439560       11531.962733      11593.290076
4     2019      4    0  ...  11503.439560       11531.962733      11593.290076
...    ...    ...  ...  ...           ...                ...               ...
2546  2019      4    0  ...  11789.571092       11531.962733      11504.536007
2547  2019      4    0  ...  11621.935185       11552.820513      11504.536007
2548  2019      4    0  ...  11621.935185       11552.820513      11504.536007
2549  2019      4    0  ...  11689.899441       11707.037037      11647.177469
2550  2019      4    3  ...  11689.525424       11625.743119      11504.536007

[2551 rows x 8 columns]

In [ ]:
pred = clf.predict_proba(df_ML_test.drop(columns='Opportunity_ID'))
pred

array([[0.19460135, 0.80539865],
       [0.19460135, 0.80539865],
       [0.19460135, 0.80539865],
       ...,
       [0.19460135, 0.80539865],
       [0.19460135, 0.80539865],
       [0.74159722, 0.25840278]])

Nos quedamos con las probabilidades de que la oportunidad sea exitosa (salga 1)

In [ ]:
predicciones = pd.Series(pred[:,1])
resultados = pd.concat([df_ML_test['Opportunity_ID'], predicciones], axis=1).rename(columns={0: 'Target'})


In [ ]:
resultados.head(30)

Opportunity_ID    Target
0            10689  0.805399
1            10689  0.805399
2            10689  0.805399
3            10690  0.466452
4            10690  0.805399
5            10690  0.805399
6            10690  0.805399
7            10690  0.805399
8            10691  0.805399
9            10692  0.466452
10           10692  0.466452
11           10692  0.466452
12           10692  0.466452
13           10692  0.466452
14           10692  0.466452
15           10693  0.805399
16           10694  0.805399
17           10695  0.805399
18           10695  0.805399
19           10695  0.805399
20           10696  0.805399
21           10696  0.805399
22           10696  0.805399
23           10696  0.805399
24           10697  0.805399
25           10697  0.805399
26           10697  0.805399
27           10697  0.805399
28           10697  0.805399
29           10698  0.805399

In [ ]:
res_promedio = resultados.groupby('Opportunity_ID').mean()

In [ ]:
res_promedio.reset_index(inplace=True)
res_promedio

Opportunity_ID    Target
0              10689  0.805399
1              10690  0.737609
2              10691  0.805399
3              10692  0.466452
4              10693  0.805399
...              ...       ...
1562           12364  0.805399
1563           12365  0.805399
1564           12366  0.805399
1565           12367  0.805399
1566           12368  0.258403

[1567 rows x 2 columns]

In [ ]:
((res_promedio['Opportunity_ID'].value_counts()) > 1).value_counts()

False    1567
Name: Opportunity_ID, dtype: int64

In [ ]:
res_promedio.drop_duplicates(subset='Opportunity_ID', inplace=True)
res_promedio

Opportunity_ID  Target
0              10689     1.0
1              10690     1.0
2              10691     1.0
3              10692     1.0
4              10693     1.0
...              ...     ...
1562           12364     1.0
1563           12365     1.0
1564           12366     1.0
1565           12367     1.0
1566           12368     0.0

[1567 rows x 2 columns]

HAY QUE CORREGIR ESTOS RESULTADOS YA QUE ALGUNAS OPORTUNIDADES NOS DAN QUE SON GANADAS Y PERDIDAS (BUSCAR EL PROMEDIO)

In [ ]:
res_promedio.to_csv('resultados.csv', index=False)